### 모델 훈련
개별 파일(MF.py, KNN.py)에서도 훈련이 가능하지만, 최상위 모듈인 train.py를 사용하여 학습을 진행할 수 있습니다.</br>
train.py 모듈을 터미널에서 실행하는 것으로 학습할 수 있습니다.</br>
train.py와 함께 사용할 수 있는 arguments들은 다음과 같습니다.</br>

**mf 모델 학습용 arguments**
- --mf : Matrix Factorization 모델의 학습 여부를 결정하는 인자입니다. --mf 를 입력하는 경우 학습을 진행하며, --no-mf를 입력하는 경우 해당 모델의 학습을 진행하지 않습니다.(입력하지 않았을 경우에는 학습 진행을 하도록 되어 있습니다.)
- -k : Matrix Factorization 행렬의 크기를 결정하는 인자값입니다. (default = 200)
- -e 또는 --epochs : mf 모델의 학습 횟수를 결정하는 인자입니다. (default = 1)
- -b 또는 --batch_size : 학습 시 사용하는 batch_size를 결정하는 인자입니다.(default = 512)

**knn 모델 학습용 arguments**
- --knn : 최근접 이웃을 활용한 콘텐츠 기반 필터링 모델의 학습 여부를 결정하는 인자입니다. --knn을 입력하는 경우 학습을 진행하며, word2vec 모델과 cbf_data, knn모델을 models 폴더 경로에 생성합니다.(이미 존재하는 경우에는 업데이트) --no-knn을 입력하면 해당 모델의 학습을 진행하지 않습니다.(입력하지 않았을 경우에는 학습 진행을 하도록 되어 있습니다.)
- --vector_size : word2vec 학습에 생성하는 행렬 차원의 수를 결정하는 인자입니다.(default = 100)
- --pretrained : 영화 장르 임베딩을 적용할 때 사용하는 gensim의 사전학습 모델을 결정하는 인자입니다. (default = 'glove-twitter-100')

In [19]:
#CLI
#mf모델만 3 epochs로 학습하라는 명령어(knn 모델은 학습하지 않음)
#두가지 모델을 전무 학습시키고 싶다면 !python trian.py 명령어를 사용하시면 됩니다.
!python train.py --no-mf

---Tokenizing...---
Tokenizing Complete.
---w2v Training...---
(4839, 100)
w2v Training Complete.
---pre-trained w2v loading...---

[--------------------------------------------------] 0.0% 0.0/387.1MB downloaded
[--------------------------------------------------] 0.0% 0.0/387.1MB downloaded
[--------------------------------------------------] 0.0% 0.0/387.1MB downloaded
[--------------------------------------------------] 0.0% 0.0/387.1MB downloaded
[--------------------------------------------------] 0.0% 0.0/387.1MB downloaded
[--------------------------------------------------] 0.0% 0.0/387.1MB downloaded
[--------------------------------------------------] 0.0% 0.0/387.1MB downloaded
[--------------------------------------------------] 0.0% 0.1/387.1MB downloaded
[--------------------------------------------------] 0.0% 0.1/387.1MB downloaded
[--------------------------------------------------] 0.0% 0.1/387.1MB downloaded
[--------------------------------------------------] 0.0% 

### 인기도 기반 추천 시스템 테스트
베이스라인 모델의 인기도 기반 추천은 사용자들이 가장 많이 평점을 남긴 영화 순으로 추천하도록 설계되어 있습니다.</br>
관련 코드는 models 폴더의 impersonal.py 코드에 작성되어 있습니다.

In [28]:
from models.impersonal import popular
mv_list=popular(10)
mv_list

[2858, 260, 1196, 1210, 480, 2028, 589, 2571, 1270, 593]

In [1]:
from utils.Dataloader import load_movies,load_ratings,load_users
movies_df = load_movies('datasets/')
movies_df

movieId                               title                        genres
0           1                    Toy Story (1995)   Animation|Children's|Comedy
1           2                      Jumanji (1995)  Adventure|Children's|Fantasy
2           3             Grumpier Old Men (1995)                Comedy|Romance
3           4            Waiting to Exhale (1995)                  Comedy|Drama
4           5  Father of the Bride Part II (1995)                        Comedy
...       ...                                 ...                           ...
3878     3948             Meet the Parents (2000)                        Comedy
3879     3949          Requiem for a Dream (2000)                         Drama
3880     3950                    Tigerland (2000)                         Drama
3881     3951             Two Family House (2000)                         Drama
3882     3952               Contender, The (2000)                Drama|Thriller

[3883 rows x 3 columns]

In [13]:
matching_titles=[]
for i in mv_list:
    matching_title = movies_df[movies_df['movieId'] == i]['title'].item()
    matching_titles.append(matching_title)
matching_titles

['American Beauty (1999)',
 'Star Wars: Episode IV - A New Hope (1977)',
 'Star Wars: Episode V - The Empire Strikes Back (1980)',
 'Star Wars: Episode VI - Return of the Jedi (1983)',
 'Jurassic Park (1993)',
 'Saving Private Ryan (1998)',
 'Terminator 2: Judgment Day (1991)',
 'Matrix, The (1999)',
 'Back to the Future (1985)',
 'Silence of the Lambs, The (1991)']

### 협업 필터링 모델 테스트
Matrix Factorization 기반 모델 코드의 경우 train.py를 통해 학습한 mf.h5 파일을 로드하여 예측을 진행합니다.

In [24]:
from models.MF import MF

mf = MF('./models/mf.h5')

In [25]:
userid = 1
mv_list = mf.predict(userid)
mv_list

[318, 3435, 50, 750, 2762, 745, 2858, 1207, 527, 904]

In [26]:
matching_titles=[]
for i in mv_list:
    matching_title = movies_df[movies_df['movieId'] == i]['title'].item()
    matching_titles.append(matching_title)
matching_titles

['Shawshank Redemption, The (1994)',
 'Double Indemnity (1944)',
 'Usual Suspects, The (1995)',
 'Dr. Strangelove or: How I Learned to Stop Worrying and Love the Bomb (1963)',
 'Sixth Sense, The (1999)',
 'Close Shave, A (1995)',
 'American Beauty (1999)',
 'To Kill a Mockingbird (1962)',
 "Schindler's List (1993)",
 'Rear Window (1954)']

### 콘텐츠 기반 필터링 모델 테스트
최근접 이웃 알고리즘을 활용한 콘텐츠 기반 필터링 모델의 경우 train.py를 통해 학습한 knn.joblib 파일을 로드하여 예측을 진행합니다.

In [20]:
from models.KNN import KNN

knn = KNN('models/knn.joblib')

In [21]:
USER_ID = 1
TOP_NUM=10
mv_list = knn.predict(USER_ID, TOP_NUM)
mv_list

array([1205, 2081, 2080,  258, 1566,  673, 2054, 1215,  558,   70],
      dtype=int64)

In [23]:
matching_titles=[]
for i in mv_list:
    matching_title = movies_df[movies_df['movieId'] == i]['title'].item()
    matching_titles.append(matching_title)
matching_titles

['Transformers: The Movie, The (1986)',
 'Little Mermaid, The (1989)',
 'Lady and the Tramp (1955)',
 "Kid in King Arthur's Court, A (1995)",
 'Hercules (1997)',
 'Space Jam (1996)',
 'Honey, I Shrunk the Kids (1989)',
 'Army of Darkness (1993)',
 'Pagemaster, The (1994)',
 'From Dusk Till Dawn (1996)']